# Compton Analysis Notebook

In [49]:
ANGLES_OUTPUT_PATH = r"G:\.shortcut-targets-by-id\1IcR20O5deY8V-HZhJrHf7ZL2cmAiG7GY\ComptonMeasurements\Angles"
ENERGY_CHANNEL_CALIBRATION_PATH = r"G:\.shortcut-targets-by-id\1IcR20O5deY8V-HZhJrHf7ZL2cmAiG7GY\ComptonMeasurements\EnergyChannel"
MCA_FILE_EXTENSION = ".mca"
MCA_FIRST_NON_ZERO_CHANNEL = 568

%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [3]:
import os
import pathlib
import mca_output
import plotly_utils

def find_mca_files_in_folder(folder: str) -> list[pathlib.Path]:
    folder_path = pathlib.Path(folder)
    return [pathlib.Path.joinpath(folder_path, out_file) for out_file in os.listdir(folder) if pathlib.Path(out_file).suffix == MCA_FILE_EXTENSION]

# Find all MCA files in given folder
if not os.path.exists(ANGLES_OUTPUT_PATH) or not os.path.isdir(ANGLES_OUTPUT_PATH):
    raise FileNotFoundError(f"Directory \"{ANGLES_OUTPUT_PATH}\" does not exist")

angle_calibration_mca_files = find_mca_files_in_folder(ANGLES_OUTPUT_PATH)
angle_calibration_mca_outs = [mca_output.parse_output_file(mca_file.absolute()) for mca_file in angle_calibration_mca_files]


In [4]:
for mca_out in angle_calibration_mca_outs:
    fig = plotly_utils.generate_mca_out_figure(mca_out, pathlib.Path(mca_out.path).stem)
    fig.show()

### Extract Maximum Intensity for Each Angle

The following excerpt extracts the bin with the highest count number around the 3000 region.

In [5]:
import numpy as np

for mca_out in angle_calibration_mca_outs:
    channel_count = np.array(mca_out.channel_count_list, np.float32) / mca_out.measurement_time
    max_index = np.argmax(channel_count)
    max_counts = channel_count[max_index]
    print(f"{pathlib.Path(mca_out.path).stem}: channel: {max_index}, counts: {max_counts}")

angle_2.5: channel: 2916, counts: 163.4600067138672
angle_-10: channel: 2844, counts: 12.600000381469727
angle_7.5: channel: 2930, counts: 182.10000610351562
angle_5: channel: 2930, counts: 177.69000244140625
angle_0: channel: 2930, counts: 134.7899932861328
angle_20: channel: 2894, counts: 51.5099983215332
angle_-5: channel: 2891, counts: 64.52999877929688
angle_25: channel: 2870, counts: 6.869999885559082
angle_15: channel: 2912, counts: 124.7300033569336
angle_10: channel: 2920, counts: 173.4499969482422
angle_-15: channel: 2833, counts: 0.9300000071525574


We can see from the above that indeed at the angle 7.5 degrees the most counts per unit time (100s live time) is measured at around bin 2930.

### Fitting a Gaussians for Compton Spectrum & Gamma Decay Peak

In [6]:
import typing
import curve_fitter
import analysis_utils

filter_7_5_measurement: typing.Callable[[mca_output.MCAOutput], bool] = lambda mca_out: pathlib.Path(mca_out.path).stem == "angle_7.5"
targetless_7_5_measurement = next((mca_out for mca_out in angle_calibration_mca_outs if filter_7_5_measurement(mca_out)), None)

if not targetless_7_5_measurement:
    raise RuntimeError("Measurment not found")

channel_counts = np.array(targetless_7_5_measurement.channel_count_list) / targetless_7_5_measurement.measurement_time
channel_counts_uncertainty = np.sqrt(channel_counts)

MEASUREMENT_LENGTH = len(channel_counts)

channel_index = np.arange(MEASUREMENT_LENGTH, dtype=np.float32)
channel_uncertainty = np.full([MEASUREMENT_LENGTH], 1./np.sqrt(3))

gaussian_peak_model_data = curve_fitter.ModelData(channel_index[2930-200:2930+200], channel_counts_uncertainty[2930-200:2930+200], channel_counts[2930-200:2930+200], channel_counts_uncertainty[2930-200:2930+200])

beta, sd, chi_sq, p_value = curve_fitter.odr_fit_gaussian(gaussian_peak_model_data, [2930, 100, 40000])
initial_guess_model = curve_fitter.vectorized_gaussian(2930, 100, 40000)
initial_guess_data = initial_guess_model(np.arange(MEASUREMENT_LENGTH, dtype=np.float32))
gaussian_peak_odr_data = curve_fitter.vectorized_gaussian(beta[0], beta[1], beta[2])(np.arange(MEASUREMENT_LENGTH, dtype=np.float32))
print("Gaussian Peak fitting data: ", beta, sd, chi_sq, p_value, "\n")

compton_spectrum_model_data = curve_fitter.ModelData(channel_index[600:2400], channel_counts_uncertainty[600:2400], channel_counts[600:2400], channel_counts_uncertainty[600:2400])
first_gaussian_initial_guess = [900 , 380, np.sum(channel_counts[735:925])*2]
second_gaussian_initial_guess = [1980, 360, np.sum(channel_counts[1900:2080])*2]

print(f"Normalization guesses: {np.sum(channel_counts[735:925])*2}, {np.sum(channel_counts[1900:2080])*2}")
beta, sd, chi_sq, p_value = curve_fitter.odr_fit_two_gaussian_sum(compton_spectrum_model_data, first_gaussian_initial_guess+second_gaussian_initial_guess)
print(f"Compton spectrum fitting data:\nFirst gaussian: values: {beta[0:3]}, errors: {sd[0:3]}\nSecond gaussian: values: {beta[3:]}, errors: {sd[3:]}\nChi-sq: {chi_sq}, p-value: {p_value}")
compton_spectrum_odr_data = curve_fitter.vectorized_two_gaussian_sum(beta)(np.arange(MEASUREMENT_LENGTH, dtype=np.float32))

fig = plotly_utils.generate_scatter_and_line_plot(channel_counts, gaussian_peak_odr_data, compton_spectrum_odr_data)
fig.update_layout(height=800)
fig.show()

background_noise, noise_uncertainty = analysis_utils.find_background_noise(channel_counts[4200:6100])

Gaussian Peak fitting data:  [ 2927.54656851   104.93651132 46784.93067335] [ 0.11047535  0.10303988 42.759325  ] 0.02108790325893657 1.0 

Normalization guesses: 5435.26, 5634.0
Compton spectrum fitting data:
First gaussian: values: [  984.3736844    355.7771356  13854.53620126], errors: [  4.27457214   5.06524425 213.75229392]
Second gaussian: values: [ 1829.36709104   318.96962047 13092.08414216], errors: [  4.29904569   2.71489828 179.92232315]
Chi-sq: 0.058869743912641125, p-value: 1.0


In [123]:
import analysis_utils
model_data = analysis_utils.generate_model_data_from_mca_output(targetless_7_5_measurement)

first_compton_gaussian_guess = curve_fitter.GaussianFittingParameters(900 , 300, np.sum(model_data.y_data[735:925])*4)
second_compton_gaussian_guess = curve_fitter.GaussianFittingParameters(2000, 300, np.sum(model_data.y_data[1900:2080])*4)
main_peak_guess = curve_fitter.GaussianFittingParameters(2930, 100, 48000)

gaussian_sum_model_data = curve_fitter.ModelData(model_data.x_data[MCA_FIRST_NON_ZERO_CHANNEL:], model_data.x_error[MCA_FIRST_NON_ZERO_CHANNEL:], model_data.y_data[MCA_FIRST_NON_ZERO_CHANNEL:], model_data.y_error[MCA_FIRST_NON_ZERO_CHANNEL:])
fitting_datas, uncertainties, chi_sq, p_value  = curve_fitter.odr_fit_gaussian_sum(gaussian_sum_model_data, [first_compton_gaussian_guess, second_compton_gaussian_guess, main_peak_guess])

analysis_utils.print_guassian_sum_fit_output(fitting_datas, uncertainties, chi_sq, p_value)

fitted_line_data = curve_fitter.vectorized_gaussian_sum(fitting_datas)(channel_index)
fig = plotly_utils.generate_scatter_and_line_plot(model_data.y_data, fitted_line_data)

fig.update_layout(height=800)
fig.show()

Gaussian #1: Fitting Params: GaussianFittingParameters(mean=np.float64(878.6049330852377), std_dev=np.float64(280.3532778830761), normalization=np.float64(8894.71825282978)), Uncertainties: (np.float64(13.20508940290369), np.float64(14.924239367718675), np.float64(728.2696661980083))
Gaussian #2: Fitting Params: GaussianFittingParameters(mean=np.float64(1716.947250783145), std_dev=np.float64(439.5502335928257), normalization=np.float64(18325.076619139876)), Uncertainties: (np.float64(19.286997366096696), np.float64(13.409276289070977), np.float64(675.3986192948419))
Gaussian #3: Fitting Params: GaussianFittingParameters(mean=np.float64(2930.48437783922), std_dev=np.float64(111.26845849955406), normalization=np.float64(47298.43484133747)), Uncertainties: (np.float64(0.5761268386237964), np.float64(0.467263425283026), np.float64(241.43987807270236))
Chi sq: 1.1903798074808876, P-Value: 1.0


## Energy Channel Calibration

In [126]:
mca_energy_channel_files = find_mca_files_in_folder(ENERGY_CHANNEL_CALIBRATION_PATH)
mca_outs = [mca_output.parse_output_file(mca_file) for mca_file in mca_energy_channel_files]

for mca_out in mca_outs:
    fig = plotly_utils.generate_mca_out_figure(mca_out, pathlib.Path(mca_out.path).stem)
    fig.update_layout(height=600)

    fig.show()

### Ba-133

In [124]:
# Ba-133 Analysis
na_22_out = next(mca_out for mca_out in mca_outs if pathlib.Path(mca_out.path).stem == "Ba133")

model_data = analysis_utils.generate_model_data_from_mca_output(na_22_out)
first_peak_guess = curve_fitter.GaussianFittingParameters(790, 130, sum(model_data.y_data[670:890])*1.4)
second_peak_guess = curve_fitter.GaussianFittingParameters(1325, 100, sum(model_data.y_data[1180:1325])*2.1)
third_peak_guess = curve_fitter.GaussianFittingParameters(1580, 60, sum(model_data.y_data[1580:3003]*1.4))

sliced_data = analysis_utils.slice_model_data(model_data, MCA_FIRST_NON_ZERO_CHANNEL, len(model_data.x_data))
fitting_datas, uncertainties, chi_sq, p_value = curve_fitter.odr_fit_gaussian_sum(sliced_data, [first_peak_guess, second_peak_guess, third_peak_guess])
analysis_utils.print_guassian_sum_fit_output(fitting_datas, uncertainties, chi_sq, p_value)

guess = curve_fitter.vectorized_gaussian_sum([first_peak_guess, second_peak_guess, third_peak_guess])(model_data.x_data)
fitted_line = curve_fitter.vectorized_gaussian_sum(fitting_datas)(model_data.x_data)
fig = plotly_utils.generate_scatter_and_line_plot(model_data.y_data, fitted_line)
fig.update_layout(height=600)
fig.show()

Gaussian #1: Fitting Params: GaussianFittingParameters(mean=np.float64(798.8327216033432), std_dev=np.float64(200.6334159548042), normalization=np.float64(301.8248017460256)), Uncertainties: (np.float64(1.3341927466226806), np.float64(1.9741537188424754), np.float64(2.150231709687516))
Gaussian #2: Fitting Params: GaussianFittingParameters(mean=np.float64(1308.5249568056447), std_dev=np.float64(89.13323073115109), normalization=np.float64(280.3933687974356)), Uncertainties: (np.float64(0.727756150670568), np.float64(0.7423075811026942), np.float64(2.2240281612932815))
Gaussian #3: Fitting Params: GaussianFittingParameters(mean=np.float64(1587.3548815013373), std_dev=np.float64(83.30205333371605), normalization=np.float64(631.6954235203266)), Uncertainties: (np.float64(0.3609134611214316), np.float64(0.28095456394914664), np.float64(2.189940373604511))
Chi sq: 0.004277421175885031, P-Value: 1.0


### Co-60

In [125]:
co_60 = next(mca_out for mca_out in mca_outs if pathlib.Path(mca_out.path).stem == "Co-60")

model_data = analysis_utils.generate_model_data_from_mca_output(co_60)
first_peak_guess = curve_fitter.GaussianFittingParameters(1084, 800, sum(model_data.y_data[813:1084])*9)
second_peak_guess = curve_fitter.GaussianFittingParameters(3830, 700, sum(model_data.y_data[3830:4400])*4)
third_peak_guess = curve_fitter.GaussianFittingParameters(5109, 173, sum(model_data.y_data[4936:5109])*3)
fourth_peak_guess = curve_fitter.GaussianFittingParameters(5770, 170, sum(model_data.y_data[5770:5940])*3)

sliced_data = analysis_utils.slice_model_data(model_data, MCA_FIRST_NON_ZERO_CHANNEL, len(model_data.x_data))
fitting_datas, uncertainties, chi_sq, p_value = curve_fitter.odr_fit_gaussian_sum(sliced_data, [first_peak_guess, second_peak_guess, third_peak_guess, fourth_peak_guess])
analysis_utils.print_guassian_sum_fit_output(fitting_datas, uncertainties, chi_sq, p_value)

guess = curve_fitter.vectorized_gaussian_sum([first_peak_guess, second_peak_guess, third_peak_guess, fourth_peak_guess])(model_data.x_data)
fitted_line = curve_fitter.vectorized_gaussian_sum(fitting_datas)(model_data.x_data)
fig = plotly_utils.generate_scatter_and_line_plot(model_data.y_data, fitted_line)
fig.update_layout(height=600)
fig.show()

Gaussian #1: Fitting Params: GaussianFittingParameters(mean=np.float64(1216.0112859025473), std_dev=np.float64(823.6584631102414), normalization=np.float64(677.3781389903161)), Uncertainties: (np.float64(4.326552955954067), np.float64(7.138726452393283), np.float64(5.757868236328959))
Gaussian #2: Fitting Params: GaussianFittingParameters(mean=np.float64(3634.463268092683), std_dev=np.float64(951.2557462819975), normalization=np.float64(605.3650698097888)), Uncertainties: (np.float64(7.098016936541478), np.float64(4.802085280056485), np.float64(3.8316160830959087))
Gaussian #3: Fitting Params: GaussianFittingParameters(mean=np.float64(5090.624882918443), std_dev=np.float64(135.2556759245251), normalization=np.float64(248.37564360264588)), Uncertainties: (np.float64(0.4774181348482929), np.float64(0.4476339726914046), np.float64(0.8839753079913439))
Gaussian #4: Fitting Params: GaussianFittingParameters(mean=np.float64(5763.649441844362), std_dev=np.float64(145.51072494008048), normaliz

### Mn-54

In [143]:
na_22_out = next(mca_out for mca_out in mca_outs if pathlib.Path(mca_out.path).stem == "Mn-54")

model_data = analysis_utils.generate_model_data_from_mca_output(na_22_out)
first_peak_guess = curve_fitter.GaussianFittingParameters(911, 1000, sum(model_data.y_data[911:1843])*3)
second_peak_guess = curve_fitter.GaussianFittingParameters(2610, 400, sum(model_data.y_data[2610:3048])*2)
third_peak_guess = curve_fitter.GaussianFittingParameters(3650, 150, sum(model_data.y_data[3650:3816]*2.5))
fourth_peak_guess = curve_fitter.GaussianFittingParameters(6351, 200, sum(model_data.y_data[6351:6556]*2))

sliced_data = analysis_utils.slice_model_data(model_data, MCA_FIRST_NON_ZERO_CHANNEL, len(model_data.x_data))
fitting_datas, uncertainties, chi_sq, p_value = curve_fitter.odr_fit_gaussian_sum(sliced_data, [first_peak_guess, second_peak_guess, third_peak_guess, fourth_peak_guess])
analysis_utils.print_guassian_sum_fit_output(fitting_datas, uncertainties, chi_sq, p_value)

guess = curve_fitter.vectorized_gaussian_sum([first_peak_guess, second_peak_guess, third_peak_guess, fourth_peak_guess])(model_data.x_data)
fitted_line = curve_fitter.vectorized_gaussian_sum(fitting_datas)(model_data.x_data)
fig = plotly_utils.generate_scatter_and_line_plot(model_data.y_data, fitted_line)
fig.update_layout(height=600)
fig.show()

Gaussian #1: Fitting Params: GaussianFittingParameters(mean=np.float64(-1979.6750654305677), std_dev=np.float64(2596.9867133989233), normalization=np.float64(250.6468655053658)), Uncertainties: (np.float64(184.2604749803146), np.float64(52.16741522087778), np.float64(19.293512167773198))
Gaussian #2: Fitting Params: GaussianFittingParameters(mean=np.float64(2627.086337415332), std_dev=np.float64(156.33269911974222), normalization=np.float64(1.1231023092387333)), Uncertainties: (np.float64(11.398475630969083), np.float64(12.39627147055381), np.float64(0.0901236677335763))
Gaussian #3: Fitting Params: GaussianFittingParameters(mean=np.float64(3655.5141965615144), std_dev=np.float64(108.69823472813754), normalization=np.float64(7.339078309367568)), Uncertainties: (np.float64(1.2926839593605268), np.float64(1.1420103064435392), np.float64(0.08117923844660317))
Gaussian #4: Fitting Params: GaussianFittingParameters(mean=np.float64(6315.063172114676), std_dev=np.float64(148.860098195241), no

In [152]:
na_22_out = next(mca_out for mca_out in mca_outs if pathlib.Path(mca_out.path).stem == "Na22")

model_data = analysis_utils.generate_model_data_from_mca_output(na_22_out)
first_peak_guess = curve_fitter.GaussianFittingParameters(1000, 300, sum(model_data.y_data[1000:1600])*2)
second_peak_guess = curve_fitter.GaussianFittingParameters(2244, 200, sum(model_data.y_data[2244:2444])*2)
fourth_peak_guess = curve_fitter.GaussianFittingParameters(5446, 120, 3)

sliced_data = analysis_utils.slice_model_data(model_data, MCA_FIRST_NON_ZERO_CHANNEL, len(model_data.x_data))
fitting_datas, uncertainties, chi_sq, p_value = curve_fitter.odr_fit_gaussian_sum(sliced_data, [first_peak_guess, second_peak_guess, fourth_peak_guess])
analysis_utils.print_guassian_sum_fit_output(fitting_datas, uncertainties, chi_sq, p_value)

guess = curve_fitter.vectorized_gaussian_sum([first_peak_guess, second_peak_guess, fourth_peak_guess])(model_data.x_data)
fitted_line = curve_fitter.vectorized_gaussian_sum(fitting_datas)(model_data.x_data)
fig = plotly_utils.generate_scatter_and_line_plot(model_data.y_data, fitted_line)
fig.update_layout(height=600)
fig.show()

Gaussian #1: Fitting Params: GaussianFittingParameters(mean=np.float64(-9782.53131477647), std_dev=np.float64(3952.1535659636165), normalization=np.float64(10433.376824076247)), Uncertainties: (np.float64(2215.979129512073), np.float64(363.4182810498489), np.float64(9805.871550949598))
Gaussian #2: Fitting Params: GaussianFittingParameters(mean=np.float64(2239.169506902721), std_dev=np.float64(83.0688050622687), normalization=np.float64(19.425633149903312)), Uncertainties: (np.float64(1.0954194815816194), np.float64(0.962143172048176), np.float64(0.23843165990235585))
Gaussian #3: Fitting Params: GaussianFittingParameters(mean=np.float64(5445.486837204028), std_dev=np.float64(130.8453505291347), normalization=np.float64(3.6957084134497027)), Uncertainties: (np.float64(3.939650049749375), np.float64(3.4374476504812623), np.float64(0.1042764804251964))
Chi sq: 0.002142727401768035, P-Value: 1.0
